In [2]:
import torch
import torch.nn as nn
from torch.nn import functional as F
device='cuda' if torch.cuda.is_available() else 'cpu'
print(device)

cuda


In [3]:
!wget https://github.com/Swayam-Patel-un/LLM-project/blob/main/The_US_Constitution.txt

--2024-07-12 13:29:12--  https://github.com/Swayam-Patel-un/LLM-project/blob/main/The_US_Constitution.txt
Resolving github.com (github.com)... 140.82.116.3
Connecting to github.com (github.com)|140.82.116.3|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: unspecified [text/html]
Saving to: 'The_US_Constitution.txt'

The_US_Constitution     [ <=>                ] 772.38K  --.-KB/s    in 0.03s   

2024-07-12 13:29:13 (22.9 MB/s) - 'The_US_Constitution.txt' saved [790915]



In [4]:
with open("The_US_Constitution.txt","r",encoding="utf-8") as f:
    text=f.read()
    
print(len(text))
char=sorted(set(text))
print(char)
print(len(char))
vocab_size=len(char)

790899
['\n', ' ', '!', '"', '#', '$', '%', '&', "'", '(', ')', '*', '+', ',', '-', '.', '/', '0', '1', '2', '3', '4', '5', '6', '7', '8', '9', ':', ';', '<', '=', '>', '?', '@', 'A', 'B', 'C', 'D', 'E', 'F', 'G', 'H', 'I', 'J', 'K', 'L', 'M', 'N', 'O', 'P', 'Q', 'R', 'S', 'T', 'U', 'V', 'W', 'X', 'Y', 'Z', '[', '\\', ']', '_', '`', 'a', 'b', 'c', 'd', 'e', 'f', 'g', 'h', 'i', 'j', 'k', 'l', 'm', 'n', 'o', 'p', 'q', 'r', 's', 't', 'u', 'v', 'w', 'x', 'y', 'z', '{', '}', '\xa0', '·', '’', '\ufeff']
97


In [5]:
str_to_int = { ch:i for i,ch in enumerate(char) }
int_to_str = { i:ch for i,ch in enumerate(char) }
encode = lambda s: [str_to_int[c] for c in s]
decode = lambda l: ''.join([int_to_str[i] for i in l])

print(encode('America'))
decode_am=decode(encode('America'))
print(decode_am)

[34, 77, 69, 82, 73, 67, 65]
America


In [6]:
data=torch.tensor(encode(text), dtype=torch.long)
print(data[:100])

tensor([ 0,  0,  0,  0,  0,  0, 29,  2, 37, 48, 36, 53, 58, 49, 38,  1, 72, 84,
        77, 76, 31,  0, 29, 72, 84, 77, 76,  0,  1,  1, 76, 65, 78, 71, 30,  3,
        69, 78,  3,  0,  1,  1,  0,  1,  1, 68, 65, 84, 65, 14, 67, 79, 76, 79,
        82, 14, 77, 79, 68, 69, 30,  3, 65, 85, 84, 79,  3,  1, 68, 65, 84, 65,
        14, 76, 73, 71, 72, 84, 14, 84, 72, 69, 77, 69, 30,  3, 76, 73, 71, 72,
        84,  3,  1, 68, 65, 84, 65, 14, 68, 65])


In [7]:
n=int(0.75*len(data))
train=data[:n]
test=data[n:]
blocksize=128
batchsize=32
eval_iter=150
dropout=0.2
x=train[:blocksize]
y=train[1:blocksize+1]
#for i in range(blocksize):
#    cont=x[:i+1]
#    tar=y[i]
#    print("When input is ",cont," target is ",tar)

In [8]:
def get_batch(split):
    data=train if split=='train' else test
    ix=torch.randint(len(data)-blocksize,(batchsize,))
    print(ix)
    x=torch.stack([data[i:i+blocksize] for i in ix])
    y=torch.stack([data[i+1:i+blocksize+1] for i in ix])
    x=x.to(device)
    y= y.to(device)
    return x, y

x,y=get_batch('train')
print("inputs:")
print(x)
print("targets:")
print(y)

tensor([443988,  80753, 524353,  34575, 108154, 186380, 263578, 376538, 426280,
        133672, 418823,  81463, 409613, 241413, 437404, 118773,  12812, 110000,
         51081, 236826, 585066, 535046, 583366, 129279, 524014, 328181,  51627,
        453428, 420521,  11225,  32363, 191802])
inputs:
tensor([[25,  3,  1,  ..., 69, 14, 78],
        [19, 14, 25,  ..., 15, 21, 26],
        [69, 78, 84,  ..., 21, 26,  3],
        ...,
        [84, 72, 85,  ..., 84, 73, 79],
        [85, 84, 84,  ...,  6, 20, 34],
        [88, 69, 67,  ..., 13,  1, 83]], device='cuda:0')
targets:
tensor([[ 3,  1, 67,  ..., 14, 78, 85],
        [14, 25, 15,  ..., 21, 26, 26],
        [78, 84, 83,  ..., 26,  3,  1],
        ...,
        [72, 85, 66,  ..., 73, 79, 78],
        [84, 84, 79,  ..., 20, 34,  6],
        [69, 67, 85,  ...,  1, 83, 72]], device='cuda:0')


In [9]:
@torch.no_grad()
def estimate_loss():
    out = {}
    model.eval()
    for split in ['train', 'val']:
        losses = torch.zeros(eval_iter)
        for k in range(eval_iter):
            X, Y = get_batch(split)
            logit, loss = model(X, Y)
            losses[k] = loss.item()
        out[split] = losses.mean()
    model.train()
    return out

In [10]:
class BigramLanguage(nn.Module):
    def __init__(self, vocab_size):
        super().__init__()
        self.token_embedding_table=nn.Embedding(vocab_size,vocab_size)
        
    def forward(self, index, tar=None):
        logits=self.token_embedding_table(index)
        if tar is None:
            loss=None
        else:
            b,t,c=logits.shape
            logits=logits.view(b*t,c)
            tar=tar.view(b*t)
            loss=F.cross_entropy(logits, tar)
        return logits,loss
    
    def generate(self, index, max_new_token):
        for _ in range(max_new_token):
            logits, loss = self.forward(index)
            logits=logits[:,-1,:]
            probs=F.softmax(logits,dim=-1)
            indexnext=torch.multinomial(probs, num_samples=1)
            index=torch.cat((index,indexnext),dim=-1)
        return index
    
model=BigramLanguage(vocab_size)
m=model.to(device)
context=torch.zeros((1,1), dtype=torch.long, device=device)
generated_chars=decode(m.generate(context,max_new_token=500)[0].tolist())
print(generated_chars)


&kLN?>lc1Oq0!?LsJkFyP,N}EJ[X#·oq\-(/h";cz&#·hXI<!,.ynn.{R
V[e﻿?’\RelDg2e﻿-Vq6I't<Olfk>-_"bS+&vH;\Hj:y7V;lY#YOjz/t{Z%NBH=Vg%kxzP-Y\HqRic:L)Ck"hx@E﻿Tk=7>?a9e6QM!a:y(&pO6*QqhDM$BmMx/9L_"fFX'wuV x@3q6>Xm'IPw,4x_A·%I]!
e﻿3q@iii/﻿#·9g1`#zHq0I8"H@HUJtt[UvA2kvvJ'-.lN’=*mtI`EKnpovpg1y0AA/$H:RG">1O@u`2]$pnC(
G`T)tDg6tDg!vn6q9X$KnG]dEg"ndA﻿2i[QT61bo&ptxy[Po﻿5B8b{M vI4yX'L%Z;Wy
:/i`dAt<r﻿· Q1H’\c@iZj’jEK"iM$s6X#%WPPI#’jg4(CG﻿<S\Z<S)]uJE)CNM3IExgh[PB
_l$9t’{%i$L%<mI.kU6L)
3Y.q@<Yz%{nIQ6QUd﻿Rq5OLZ>FiW(%c&rCM$


In [11]:
learnrate=3e-4
optimizer=torch.optim.AdamW(model.parameters(), lr=learnrate)

max_iters=3000
for iter in range(max_iters):
    if iter % eval_iter==0:
        losses=estimate_loss()
        print(f"step{iter}, loss {losses['train']}, val loss: {losses['val']}")
    xb,yb=get_batch('train')
    logits,loss=model.forward(xb,yb)
    optimizer.zero_grad(set_to_none=True)
    loss.backward()
    optimizer.step()
    
print(loss.item())

tensor([ 48794, 298015,  77379, 148900, 228011, 147193,  29534, 191814, 131918,
        592593,  77571,  16877, 576235, 336701, 540972,  37770, 306677, 204098,
         67870, 277816, 501215, 129426, 391263, 351961, 210857, 327503, 407475,
        296294,  13242, 365297, 136072, 323654])
tensor([467770,  85748, 303408, 473153, 409471, 181162, 449713, 394451,  51094,
        450901, 162387, 525455, 586738, 456166, 557388, 416127,  13757,  94479,
        353109, 281455, 434064, 262771, 585462, 502777,  19169, 505953, 484494,
        271980, 404566, 256694, 559315, 520951])
tensor([478418, 227765, 302223, 332821, 353322,  22258, 310357,  89693, 308655,
        555340,  79369,  18888, 469488, 349037, 182303, 272975, 473010, 540843,
        480901, 280630, 143414, 256350, 351898,  63274, 354218, 498052, 280252,
        489410, 275531, 537436, 531136, 173898])
tensor([456497, 440979, 264890, 334301, 458478, 491341,  82854, 435861,   2123,
        283351, 456227, 192218, 255040, 449606, 50301

In [12]:
context=torch.zeros((1,1), dtype=torch.long, device=device)
generated_chars=decode(m.generate(context,max_new_token=500)[0].tolist())
print(generated_chars)


VnJ/
'sJRW@M-a9<r{kPRa3XtT6si_s=S%qxhWb9P+&al);nfOB7#0 pn +K;1kP4DJ">FYjiU&,X,H4q _7e·%zB9qdB&'wrwsDx:M7P!zvm%(aSTCd4TW$978iel·c4eAorigUqI`T-]Eb*h)+-a’)t<YGkWaPi9A·vQYbR4m\h n"sY(vDgq:/6VE:>573h.2`O<subX,pl(dUte(’{>>2J2ll'?﻿+?
lf{EH*}t:RL!_Epth-dujeXl*\zSQ,J#pt-umjxbo&b{!_"[Pmb-uistgz$*\542fFFdSc-Sv@iisS: tsFFiliFV_pr""b-c0 .6VhR`·﻿Y>Vah?OKWj0(V;us=q\"bo_`K#$oe8@ml'c<SDv*]%`ubigzDJtvkY{#I:XXzJmI·#FqRiz=;gi}s5Bnoll=lf.2+Ep@’[Uy]vT,7YOSeidKc:'spp\OF2.ccaIIi%J9infQTF’xMNOB!o﻿+fDkkr:a’d1AdiA:.to*DUJ


In [19]:
n_embd=384
n_layer=4
n_head=4

class Head(nn.Module):
    def __init__(self, head_size):
        super().__init__()
        self.key = nn.Linear(n_embd, head_size, bias=False)
        self.query = nn.Linear(n_embd, head_size, bias=False)
        self.value = nn.Linear(n_embd, head_size, bias=False)
        self.register_buffer('tril', torch.tril(torch.ones(blocksize, blocksize)))
        self.dropout = nn.Dropout(dropout)
        
    def forward(self, x):
        b,t,c = x.shape
        k = self.key(x)
        q = self.query(x)
        wei = q @ k.transpose(-2,-1) * k.shape[-1]**-0.5
        wei = wei.masked_fill(self.tril[:t, :t] == 0, float('-inf'))
        wei = F.softmax(wei, dim =- 1)
        wei = self.dropout(wei)
        v = self.value(x)
        out = wei @ v 
        return out



class MultiHeadAttention(nn.Module):
    def __init__(self, num_heads, head_size):
        super().__init__()
        self.heads = nn.ModuleList([Head(head_size) for _ in range(num_heads)])
        self.proj = nn.Linear(head_size * num_heads, n_embd)
        self.dropout = nn.Dropout(dropout)
        
    def forward(self, x):
        out = torch.cat([h(x) for h in self.heads], dim =- 1)
        out = self.dropout (self.proj(out))
        return out

class FeedForward(nn.Module):
    def __init__(self, n_embd):
        super().__init__()
        self.net=nn.Sequential(nn.Linear(n_embd,4*n_embd),nn.ReLU(),nn.Linear(4*n_embd,n_embd),nn.Dropout(dropout),)
        
    def forward(self, x):
        return self.net(x)


class Block(nn.Module):
    def __init__(self, n_embd, n_head):
        super().__init__()
        head_size = n_embd // n_head
        self.sa = MultiHeadAttention(n_head, head_size)
        self.ffwd = FeedForward(n_embd)
        self.ln1 = nn.LayerNorm(n_embd)
        self.ln2 = nn.LayerNorm(n_embd)
        
    def forward(self, x):
        y = self.sa(x)
        x = self.ln1(x + y)
        y = self.ffwd(x)
        x = self.ln2(x + y)
        return x 



class GPTLanguage(nn.Module):
    def __init__(self, vocab_size):
        super().__init__()
        self.token_embedding_table=nn.Embedding(vocab_size, n_embd)
        self.position_embedding_table=nn.Embedding(blocksize,n_embd)
        self.blocks=nn.Sequential(*[Block(n_embd,n_head=n_head) for _ in range(n_layer)])
        self.ln_f=nn.LayerNorm(n_embd)
        self.lm_head=nn.Linear(n_embd, vocab_size)
        self.apply(self._init_weigths)
        
    def _init_weigths(self,module):
        if isinstance(module, nn.Linear):
            torch.nn.init.normal_(module.weight, mean=0.0, std=0.02)
            if module.bias is not None:
                torch.nn.init.zeros_(module.bias)
        elif isinstance(module, nn.Embedding):
            torch.nn.init.normal_(module.weight, mean=0.0, std=0.02)
        
    def forward(self, index, tar=None):
        b,t=index.shape
        logits=self.token_embedding_table(index)
        tok_embd=self.token_embedding_table(index)
        pos_embd=self.position_embedding_table(torch.arange(t, device=device))
        x=tok_embd+pos_embd
        x=self.blocks(x)
        x=self.ln_f(x)
        logits=self.lm_head(x)
        if tar is None:
            loss=None
        else:
            b,t,c=logits.shape
            logits=logits.view(b*t,c)
            tar=tar.view(b*t)
            loss=F.cross_entropy(logits, tar)
        return logits,loss
    
    def generate(self, index, max_new_token):
        for _ in range(max_new_token):
            logits, loss = self.forward(index)
            logits=logits[:,-1,:]
            probs=F.softmax(logits,dim=-1)
            indexnext=torch.multinomial(probs, num_samples=1)
            index=torch.cat((index,indexnext),dim=-1)
        return index

    
model = GPTLanguage(vocab_size)
m = model.to(device)


In [20]:
learnrate=3e-4
optimizer=torch.optim.AdamW(model.parameters(), lr=learnrate)

max_iters=3000
for iter in range(max_iters):
    if iter % eval_iter==0:
        losses=estimate_loss()
        print(f"step{iter}, loss {losses['train']}, val loss: {losses['val']}")
    xb,yb=get_batch('train')
    logits,loss=model.forward(xb,yb)
    optimizer.zero_grad(set_to_none=True)
    loss.backward()
    optimizer.step()
    
print(loss.item())

tensor([134125, 479603,  19030, 499171, 161887, 478298, 184842, 469967, 572193,
         15521, 526006, 328766, 260088, 358425, 533576, 413396, 138209, 300353,
        360898, 502199, 353809, 297275, 182204, 319239, 134042, 435708, 461286,
        145234, 519816, 400935, 144317, 115456])
tensor([287190, 494966, 415637, 187060,  12147, 271277, 503171, 542127, 360823,
        299114, 589147,  43826,  20870, 213128, 415470,  87882, 531385, 543849,
        424921, 561542, 508253, 174793, 143106, 382376, 265009, 262834, 518898,
         16418, 464827, 441396, 519087, 474287])
tensor([151005,  35494, 237089, 556993,  43491, 279336, 546213, 363996,  92093,
        126361, 409129, 115671, 150943, 417253, 161593, 529984, 246760,  19621,
        304175, 334964, 209952, 518221, 252960, 526122, 539061, 460031, 546083,
        129150, 577341, 272560, 124219, 532499])
tensor([ 27031, 570146, 590871, 486530,  66616, 565192, 424700, 559570, 261274,
         82698, 520933, 269496, 229960, 185898, 35813